# Différences finies: problèmes instationnaires 1D
 
Dans ce notebook, on donne des exemples de codes pour résoudre des problèmes instationnaires utilisant la méthode des différences finies. Pour visualiser les solutions, on utilise des animations.

## Apprendre a faire des animations (drawnow)

### Installer la librairie drawnow (le faire une fois)

En Python, il existe une librairie `drawnow` qui permet de raffraichir une fenêtre de figure pendant l'avancement d'un calcul. On utilise cette librairie pour montrer l'avancement de la solution. Pour installer cette librairie chez vous, ouvrir un terminal, puis écrire

`>> pip install drawnow`

cette commande télécharge le paquet et le pose au bon endroit dans votre distribution Python. (Parfois il faut utiliser `pip3` au lieu de `pip`). Une fois ceci est fait, vous pouvez utiliser la librairie en l'important. 

### Activer la visualisation sur une fenêtre de figure séparée

En jupyter notebook, il faut ajouter quelques instructions, qui indiquent que les graphes se feront dans une fenêtre de figure séparée. Réaliser les opérations vous-même avant de démarrer le notebook. 

- **Sous mac (bigsur chez moi)**, executer les deux prochaines cellules (vous ne pouvez pas les grouper, bizarrement). Ca revient à désactiver matplotlib dans le notebook (avec le %). 

In [1]:
#sous mac, d'abord cette cellule
import matplotlib.pyplot as plt
%matplotlib tk

In [2]:
#puis celle-ci
%matplotlib notebook

Ne tentez pas de grouper les instructions dans une même cellule. Pour une raison bizarre ça ne fonctionne pas.

- **Sous linux**, il suffit d'exectuer la cellule suivante. 

In [ ]:
#sous linux, executer cette cellule
import matplotlib.pyplot as plt
%matplotlib notebook

- **Sous Windows**, il faudra que vous trouvez la solution, je ne la connais pas. Tentez  

In [ ]:
#sous windowns, tenter d'executer cette cellule, je ne sais pas si ça fonctionne
import matplotlib.pyplot as plt
%matplotlib notebook

### Exemple d'animation

Dans cet exemple, on affiche la fonction $\sin (x-at)$ à de différents instants $t$ pour $x\in [0,L]$. On utilise pour cela, la commande drawnow qui rafraichit en permanence les images. Le graphe doit se faire de manière obligatoire dans une fonction. 

In [4]:
#importer les librairies
import numpy as np
from drawnow import drawnow, figure

#cette fonction fait la figure, elle utilise des variables définies plus bas
def makefig():
    #graphiquement
    plt.plot(x,f,'o-')
    plt.title('animation de sin(x-at) pour t = '+f'{t:4.2f}')
    plt.xlabel('x')
    
    
#maillage 
L=10      #domaine
M=100     #nombre d'intervalles spatiales
x=np.linspace(0,L,M+1)  #maillage x

#vitesse d'advection
a=1

T=5     #durée
N=100   #nombre de pas de temps    

#realiser l'animation
figure(1)
for t in np.linspace(0,T,N+1):   #pour t dans [0,T/N,2T/N, ...,T ]
    f=np.sin(x-a*t)
    drawnow(makefig)

## Problème 2.1 du cours: équation d'advection par schéma upwind

On cherche à résoudre le problème d'advection

$$
\frac{\partial f}{\partial t} + a  \frac{\partial f}{\partial x} = 0 \quad , \quad (x,t) \in [0,L] \times [0,T]
$$

Ici on note $a>0$ la vitesse d'advection. Si on fournit une condition initiale

$$
CI \ : \ f(x,0) = F(x)
$$

et une condition aux limite à l'entrée du domaine 

$$
CL \ : \ f(0,t) = F(-at)
$$

alors la solution générale de cette équation sera $F (x- at)$. La fonction $F$ est tout simplement propagé vers des 
$x$ croissants. On choisira $F (x) = \cos(x) $ dans l'exercice. 

On résolve ce problème à l'aide d'une méthode de différences finies. On suppose un maillage uniforme

$$
x_j = j \delta x \ , \ j = 0,1,\ldots,M \quad \mbox{avec} \quad \delta x = \frac{L}{M}
$$

et des pas de temps constants

$$
t_n = n \delta t \ , \ n = 0,1,\ldots,N \quad \mbox{avec} \quad \delta t = \frac{T}{N}
$$

et on notera $f(x_j,t_n) = f_j^n $. Si on utilise un schéma explicite UPWIND pour résoudre ce problème, la discrétisation du problème donne le problème matriciel suivant. On initialise 

$$
\underbrace{\left [\begin{array}{c} f_0^0 \\ f_1^0 \\ \vdots  \\ f_M^0 \end{array}\right ]}_{\mathbf{f}^0}  = \left [\begin{array}{c} F (x_0) \\ F (x_1) \\ \vdots \\  F (x_M ) \end{array}\right ]
$$

Ensuite pour tout $n = 0,1,\ldots,N-1$ on itère sur le schéma 

$$
\underbrace{\left [\begin{array}{c} f_0^{n+1} \\ f_1^{n+1} \\ \vdots  \\ f_M^{n+1} \end{array}\right ]}_{\mathbf{f}^{n+1}} = 
 \underbrace{\left [ \begin{array}{cccc} 
 0 \\ C & 1-C &  \\
  & \ddots & \ddots &   \\
   & & C & 1-C \end{array} \right ]}_{\mathcal{E}} \underbrace{\left [\begin{array}{c} f_0^{n} \\ f_1^{n} \\ \vdots  \\ f_M^{n} \end{array}\right ]}_{\mathbf{f}^{n}}  + \underbrace{\left [\begin{array}{c} F (-a t^{n+1} ) \\ 0 \\ \vdots \\  0 \end{array}\right ]}_{\mathbf{g}^{n+1}}
$$

Ici on note $C = a \delta t / \delta x $. 

In [11]:
#1. importer les librairies
import numpy as np
from drawnow import drawnow, figure

#2. fonction pour faire l'animation
def makefig():
    #graphiquement
    plt.plot(x,f,label='num')
    plt.plot(x,f_ex,label='exact')
    plt.title('solution pour t = '+f'{t[n+1]:4.2f}')
    plt.ylim([-1.2,1.2])
    plt.legend()
    plt.xlabel('x')

#3. parametres
#taille du domaine/temps final
L=10
T=10

#vitesse d'advection
a=1.1

#nombre de points et temps discrets (-1)
M=50
N=100

#pas de temps, pas d'espace et C
dx=L/M
dt=T/N

C=a*dt/dx

#maillage/temps discrets
x=np.linspace(0,L,M+1)
t=np.linspace(0,T,N+1)

#4.matrice E d'évolution et vecteur F
E=np.zeros([M+1,M+1])
for j in range(1,M+1):   #pour j allant de 1 à M
    E[j,j-1]=C
    E[j,j]=1-C
    
#vecteur F du système, sera mis à jour dans la boucle
F=np.zeros(M+1)

#5. initialisation  F(x) = cos (x) à l'instant t=0
f=np.sin(x)

 
#6. boucle d'avancement temporel
for n in range(N):   #pour n allant de 0 a N-1
    
    #mise à jour du vecteur F
    F[0]=np.sin(-a*t[n+1]) 
    
    #mise à jour du vecteur f
    f=np.dot(E,f)+F
    
    #solution exacte
    f_ex=np.sin(x-a*t[n+1]) 
    
    #vis
    drawnow(makefig)
    
print(C)

0.55


Pour $C\geq 1$, le code devient numériquement instable. On étudiera la stabilité numérique de manière théorique à l'aide de l'analyse de Fourier. 

## Problème 2.2. du cours: équation de diffusion, Crank-Nicolson

On cherche à résoudre l'équation de diffusion

$$
\frac{\partial f}{\partial t} = \alpha  \frac{\partial^2 f}{\partial x^2} \quad , \quad (x,t) \in [0,L] \times [0,T]
$$

Ici on note $\alpha>0$ le coefficient de diffusion. On fournit une condition initiale

$$
CI \ : \ f(x,0) = 0
$$

et deux conditions aux limites aux extrémités du domaine 

$$
CL \ : \ f(0,t) = 0 \ , \  f(L,t) = 1
$$
 

On résolve ce problème à l'aide d'une méthode de différences finies. On suppose un maillage uniforme et des pas de temps constants

$$
x_j = j \delta x \ , \ j = 0,1,\ldots,M \quad \mbox{avec} \quad \delta x = \frac{L}{M}
$$
$$
t_n = n \delta t \ , \ n = 0,1,\ldots,N \quad \mbox{avec} \quad \delta t = \frac{T}{N}
$$

et on notera $f(x_j,t_n) = f_j^n $. Si on utilise un schéma implicite de type CRANK-NICOLSON pour résoudre ce problème, la discrétisation du problème donne le problème matriciel suivant. On initialise 

$$
\underbrace{\left [\begin{array}{c} f_0^0 \\ f_1^0 \\ \vdots  \\ f_M^0 \end{array}\right ]}_{\mathbf{f}^0}  = \left [\begin{array}{c} 0 \\ 0 \\ \vdots \\ 0 \end{array}\right ]
$$

Ensuite pour tout $n = 0,1,\ldots,N-1$ on itère sur le schéma 

$$
\underbrace{\left [ \begin{array}{ccccc} 
 1 \\ -S/2 & 1+S & -S/2  \\
  & \ddots & \ddots & \ddots   \\
   & &  -S/2 & 1+S & -S/2 \\
   & & & & 1\end{array} \right ]}_{\mathcal{O}_g}   
\underbrace{\left [\begin{array}{c} f_0^{n+1} \\ f_1^{n+1} \\  \vdots  \\ f_{M-1}^{n+1}  \\ f_M^{n+1} \end{array}\right ]}_{\mathbf{f}^{n+1}} = \underbrace{\left [ \begin{array}{ccccc} 
 0 \\ S/2 & 1-S & S/2  \\
  & \ddots & \ddots & \ddots   \\
   & &  S/2 & 1-S & S/2 \\
   & & & & 0\end{array} \right ]}_{\mathcal{O}_d}    
\underbrace{\left [\begin{array}{c} f_0^{n} \\ f_1^{n} \\  \vdots  \\ f_{M-1}^{n}  \\ f_M^{n} \end{array}\right ]}_{\mathbf{f}^{n+1}} + \underbrace{\left [\begin{array}{c} 0 \\ 0 \\ \vdots \\ 0 \\ 1 \end{array}\right ]}_{\mathbf{g}^{n+1}}
$$

Ici on note $S = \alpha \delta t / \delta x^2 $. A chaque pas de temps, il faut résoudre le système linéaire $ \mathcal{O}_d   \mathbf{f}^{n+1}  = \mathcal{O}_g   \mathbf{f}^{n} + \mathbf{g}^{n+1}$ pour trouver $ \mathbf{f}^{n+1}$. 


In [15]:
#1. importer les librairies
import numpy as np
import matplotlib.pyplot as plt
from drawnow import drawnow, figure

def makefig():
    #graphiquement
    plt.plot(x,f,'o-')
    plt.title('solution pour t = '+f'{t[n+1]:4.2f}')
    plt.xlabel('x')

#2. définir constantes/paramètres 
L=10
alpha=50 # 10
T=20

M=100 # 30
dx=L/M

N=50 # 200
dt=T/N

S=alpha*dt/dx**2

#3. Maillage et temps
x=np.linspace(0,L,M+1)
t=np.linspace(0,T,N+1)

#4. Matrice Og et Od et vecteur g
Og=np.zeros([M+1,M+1])
Od=np.zeros([M+1,M+1])
g=np.zeros(M+1)
  
#corriger les lignes des pts de bords (0 et M)
Og[0,0]=1
Og[M,M]=1
g[M]=1

#boucle pour les points int
for j in range(1,M):   #pour j allant de 1 à M-1 (M n'est pas atteint)
    Og[j,[j-1,j,j+1]]=[-S/2,1+S,-S/2]
    Od[j,[j-1,j,j+1]]=[ S/2,1-S, S/2]
    
    ##equivalent pour Og
    #Og[j,j-1]=-S/2
    #Og[j,j]=1+S
    #Og[j,j+1]=-S/2

#5. initalisation
f=np.zeros(M+1)

#5. boucle temporel
for n in range(N):  #pour n allant de 0 a N-1
    
    #trouver la solution de Og .dot f_new = Od .dot f_old + g 
    membrededroite=np.dot(Od,f)+g
    f=np.linalg.solve(Og,membrededroite)

    drawnow(makefig)
